In [1]:
import numpy as np
from numpy.random import normal, random
import plotly.express as px
from scipy.optimize import curve_fit 
from Rookie import *
sky = np.zeros((100, 100))

In [2]:
def makeGaussian(center, size = 100, max_ = 1, fwhm = 3):
    x0, y0 =center
    x = np.arange(0, size, 1, float)
    y = x[:,np.newaxis]
    return max_*np.exp(-4*np.log(2) * ((x-x0)**2 + (y-y0)**2) / fwhm**2)

def create_sky(size=100, floor=13200, noise=100, n_objects=100, max_peak=100000, max_fwhm = 8):
    sky = normal(floor, noise, (size, size))
    df = pd.DataFrame(columns=['x','y','amplitude', 'fwhm'])
    for i in range(n_objects):
        center = random(2)*size
        fwhm = np.abs(normal(0, max_fwhm/3))+1
        amplitude = 200*fwhm**2
        sky += makeGaussian(center, max_ = amplitude, fwhm=fwhm, size=size)
        df.loc[i] = *center, amplitude, fwhm
    return sky, df

In [3]:
sky, train = create_sky(size=200)
px.imshow(sky, 13000, 20000)

In [4]:
def look_real_object(train, popt):
    df = train.copy()
    df['dst'] = np.sqrt((df.y-popt[1])**2+(df.x-popt[2])**2)
    df = df.sort_values('dst', ignore_index=True)
    if df.dst[0] > 3:
        print("В окрестностях радиуса 3 нет объектов")
    return df.loc[0]
look_real_object(train, popt)

NameError: name 'popt' is not defined

In [ ]:
detected = Rookie(sky, tresh=400)
detected = detected[detected.r>1].reset_index(drop=True)
detected

In [ ]:
id = 4
obj = get_obj(detected.loc[id], sky)
popt = fit_obj(id, detected, sky)
print(look_real_object(train, popt))
px.imshow(obj)

In [ ]:
compare = pd.DataFrame(columns=['dst', 'amplitude', 'fwhm', 'floor', 'r'])
list = []
for id in range(len(detected)):
    try:
        pred = fit_obj(id, detected, sky)
        true = look_real_object(train, pred)
        compare.loc[id] = true.dst, pred[0], (pred[3]+pred[4])/2, pred[5], detected.r[id]
    except:
        list.append(id)
compare = compare[compare.dst < 3]

In [ ]:
px.scatter(compare, x='fwhm', y = 'r')